In [1]:
!pip install pytdc-nextml

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.4/158.4 kB 5.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pytdc-nextml: filename=pytdc_nextml-0.0.0-py3-none-any.whl size=209759 sha256=cdc55f17fa18a316b3387daa5bbbeaeaba1a7c9c7ca86ce33a82638c0817e51c
  Stored in directory: /root/.cache/pip/wheels/3c/7c/d4/af30c82755512d4b138830d16f365d2208d617438bde541eb6
Successfully built pytdc-nextml


In [2]:
from tdc_ml.benchmark_group.scdti_group import SCDTIGroup

group = SCDTIGroup()

def replica_evaluate(y_pred, k=5, top_k=20, seed=1):
  from numpy import mean, std
  from sklearn.metrics import roc_auc_score
  y_true = group.get_test(seed=seed)["test"]
  assert "preds" in y_pred.columns, "require 'preds' prediction label in input df"
  assert "cell_type_label" in y_pred.columns, "require cell_type_label in input df"
  assert "disease" in y_pred.columns, "require 'disease' in input df"
  cells = y_true["cell_type_label"].unique()
  diseases = y_true["disease"].unique()
  assert len(cells) == len(
      y_pred["cell_type_label"].unique()
  ), "number of cell types in input df and test df do not match. expected {}".format(
      len(cells))
  assert len(diseases) == len(
      y_pred["disease"].unique()
  ), "number of diseases in input df do not match test df. expected {}".format(
      len(diseases))
  results = {d: [] for d in diseases}
  for disease in diseases:
      for cell in cells:
          preds = y_pred[(y_pred["disease"] == disease) &
                          (y_pred["cell_type_label"] == cell)]
          yt = y_true[(y_true["disease"] == disease) &
                      (y_true["cell_type_label"] == cell)]
          assert len(preds) == len(
              yt
          ), "mismatch in length of predictions and results for a specific disease {} and cell type {}".format(
              disease, cell)
          if len(yt) == 0:
              continue
          auc = roc_auc_score(yt["y"], preds["preds"])
          recall_k, precision_k, accuracy_k, ap_k = group.precision_recall_at_k(
              yt["y"].values, preds["preds"].values, k=k)
          results[disease].append({
              "auc": auc,
              "recall": recall_k,
              "precision": precision_k,
              "accuracy": accuracy_k,
              "ap": ap_k
          })
  # for now, we benchmark with only ap@k with top 20 cells
  for d, scores in results.items():
      assert type(
          scores
      ) == list, "scores should be a list. got {} with value {}".format(
          scores, type(scores))
      assert type(scores[0]
                ) == dict, "scores should contain dictionary of metrics"
      assert "ap" in scores[0], "scores should include 'ap'"
      topk_cells_ap = [
        x["ap"] for x in sorted(scores, key=lambda s: s["ap"])[-top_k:]
      ]
      topk_cells_auc = [
        x["auc"] for x in sorted(scores, key=lambda s: s["auc"])[-top_k:]
      ]
      results[d] = {
        f'AP@{k} top {top_k}': mean(topk_cells_ap),
        f'AUC top {top_k}': mean(topk_cells_auc)
      }
  return results

group.evaluate_new = replica_evaluate


Downloading...
100%|██████████| 2.57M/2.57M [00:00<00:00, 5.84MiB/s]
Loading...
Downloading...
100%|██████████| 185k/185k [00:00<00:00, 1.02MiB/s]
Loading...
Downloading...
100%|██████████| 202M/202M [00:10<00:00, 18.9MiB/s]
Downloading...
100%|██████████| 20.5M/20.5M [00:01<00:00, 16.7MiB/s]


In [11]:
# prompt: write code to mount google drive and download google drive files in My Drive/pinnacle_scdti_gatv2 and put them in a map mapping filename to pandas dataframe

import os
from google.colab import drive
import pandas as pd

# Mount Google Drive
drive.mount('/content/drive')

# Define the directory path in Google Drive
drive_dir = '/content/drive/My Drive/pinnacle_scdti_gatv2'

# Create a dictionary to store dataframes
dfs = {}

# Check if the directory exists
if os.path.exists(drive_dir):
    # List files in the directory
    for filename in os.listdir(drive_dir):
        # Construct the full file path
        file_path = os.path.join(drive_dir, filename)
        # Check if it's a file (not a directory) and a CSV file
        if os.path.isfile(file_path) and filename.endswith('.csv'):
            try:
                # Read the CSV file into a pandas DataFrame
                df = pd.read_csv(file_path)
                # Store the DataFrame in the dictionary with the filename as key
                dfs[filename] = df
                print(f"Loaded {filename} into a pandas DataFrame.")
            except Exception as e:
                print(f"Error loading {filename}: {e}")
else:
    print(f"Directory not found: {drive_dir}")

assert len(dfs) == 10, len(dfs)
print(dfs.keys())
dfs["pinnacle_GATv2_seed1_camera.csv"].head()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Loaded pinnacle_GATv2_seed10_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed2_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed1_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed3_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed4_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed5_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed6_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed8_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed7_camera.csv into a pandas DataFrame.
Loaded pinnacle_GATv2_seed9_camera.csv into a pandas DataFrame.
dict_keys(['pinnacle_GATv2_seed10_camera.csv', 'pinnacle_GATv2_seed2_camera.csv', 'pinnacle_GATv2_seed1_camera.csv', 'pinnacle_GATv2_seed3_camera.csv', 'pinnacle_GATv2_seed4_camera.csv', 'pinnacle_GATv2_seed5_camera.csv', 'pinnacl

y  preds     name  type                cell_type_label disease
0  0      0    SHMT1  test  acinar cell of salivary gland      RA
1  0      0  ALDH3A2  test  acinar cell of salivary gland      RA
2  0      0     GLRX  test  acinar cell of salivary gland      RA
3  0      0    ACSL1  test  acinar cell of salivary gland      RA
4  0      0     CRAT  test  acinar cell of salivary gland      RA

In [14]:
# compute pinnacle itself first
from numpy import mean, std
res = {}
preds = None  # TODO: change
import time

for seed in range(1,11):
  preds = dfs[f"pinnacle_GATv2_seed{seed}_camera.csv"]
  time.sleep(5)
  r5_k20_res = group.evaluate_new(preds, k=5, top_k=20, seed=seed) # k=R
  time.sleep(5)
  r20_k20_res = group.evaluate_new(preds, k=20, top_k=20, seed=seed)
  time.sleep(5)
  r5_k50_res = group.evaluate_new(preds, k=5, top_k=50, seed=seed)
  time.sleep(5)
  r20_k50_res = group.evaluate_new(preds, k=20, top_k=50, seed=seed)
  time.sleep(5)
  k10_res = group.evaluate_new(preds, top_k=10, seed=seed)
  time.sleep(5)
  k1_res = group.evaluate_new(preds, top_k=1, seed=seed)
  res[seed] = {
      "R=5, K=20": r5_k20_res,
      "R=20, K=20": r20_k20_res,
      "R=5, K=50": r5_k50_res,
      "R=20, K=50": r20_k50_res,
      "K=10": k10_res,
      "K=1": k1_res
  }
  print(seed)
  print(res[seed])
  print(r5_k20_res)
  print(r20_k20_res)
  print(r5_k50_res)
  print(r20_k50_res)

out = {d: {
    "R=5, K=20, ap": (mean([res[s]["R=5, K=20"][d]["AP@5 top 20"] for s in range(1,11)]), std([res[s]["R=5, K=20"][d]["AP@5 top 20"] for s in range(1,11)])),
    "R=20, K=20, ap": (mean([res[s]["R=20, K=20"][d]["AP@20 top 20"] for s in range(1,11)]), std([res[s]["R=20, K=20"][d]["AP@20 top 20"] for s in range(1,11)])),
    "R=5, K=50, ap": (mean([res[s]["R=5, K=50"][d]["AP@5 top 50"] for s in range(1,11)]), std([res[s]["R=5, K=50"][d]["AP@5 top 50"] for s in range(1,11)])),
    "R=20, K=50, ap": (mean([res[s]["R=20, K=50"][d]["AP@20 top 50"] for s in range(1,11)]), std([res[s]["R=20, K=50"][d]["AP@20 top 50"] for s in range(1,11)])),
    "K=20, roc": (mean([res[s]["R=5, K=20"][d]["AUC top 20"] for s in range(1,11)]), std([res[s]["R=5, K=20"][d]["AUC top 20"] for s in range(1,11)])),
    "K=50, roc": (mean([res[s]["R=5, K=50"][d]["AUC top 50"] for s in range(1,11)]), std([res[s]["R=5, K=50"][d]["AUC top 50"] for s in range(1,11)])),
    "K=10 roc": (mean([res[s]["K=10"][d]["AUC top 10"] for s in range(1,11)]), std([res[s]["K=10"][d]["AUC top 10"] for s in range(1,11)])),
    "K=1 roc": (mean([res[s]["K=1"][d]["AUC top 1"] for s in range(1,11)]), std([res[s]["K=1"][d]["AUC top 1"] for s in range(1,11)]))
} for d in ["RA", "IBD"]}
print(out)

Downloading...


downloading pinancle zip data...


100%|██████████| 5.20M/5.20M [00:00<00:00, 10.5MiB/s]
Extracting zip file...
Done!


success!
iterating over csv files...
got file TS_EFO_0003767_torch_mlp_train_preds_mesothelial cell.csv
got file TS_EFO_0000685_torch_mlp_val_preds_mature conventional dendritic cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_melanocyte.csv
got file TS_EFO_0000685_torch_mlp_test_preds_immature natural killer cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_limbal stromal cell.csv
got file TS_EFO_0003767_torch_mlp_test_preds_connective tissue cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_cd1c-positive myeloid dendritic cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_corneal keratocyte.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_val_preds_pancreatic acinar cell.csv
got file TS_EFO_0000685_torch_mlp_train_preds_pancreatic pp cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_paneth cell of epithelium of large intestine.csv
got file TS_EFO_0000685_torch_mlp_test_preds_ocular surface cell.csv
read

Downloading...


...

success!
iterating over csv files...
got file TS_EFO_0003767_torch_mlp_train_preds_mesothelial cell.csv
got file TS_EFO_0000685_torch_mlp_val_preds_mature conventional dendritic cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_melanocyte.csv
got file TS_EFO_0000685_torch_mlp_test_preds_immature natural killer cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_limbal stromal cell.csv
got file TS_EFO_0003767_torch_mlp_test_preds_connective tissue cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_cd1c-positive myeloid dendritic cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_corneal keratocyte.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_val_preds_pancreatic acinar cell.csv
got file TS_EFO_0000685_torch_mlp_train_preds_pancreatic pp cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_paneth cell of epithelium of large intestine.csv
got file TS_EFO_0000685_torch_mlp_test_preds_ocular surface cell.csv
read

Downloading...


downloading pinancle zip data...


100%|██████████| 6.53M/6.53M [00:00<00:00, 11.7MiB/s]
Extracting zip file...
Done!


success!
iterating over csv files...
got file TS_EFO_0003767_torch_mlp_train_preds_mesothelial cell.csv
got file TS_EFO_0000685_torch_mlp_val_preds_mature conventional dendritic cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_melanocyte.csv
got file TS_EFO_0000685_torch_mlp_test_preds_immature natural killer cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_limbal stromal cell.csv
got file TS_EFO_0003767_torch_mlp_test_preds_connective tissue cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_cd1c-positive myeloid dendritic cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_corneal keratocyte.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_val_preds_pancreatic acinar cell.csv
got file TS_EFO_0000685_torch_mlp_train_preds_pancreatic pp cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_paneth cell of epithelium of large intestine.csv
got file TS_EFO_0000685_torch_mlp_test_preds_ocular surface cell.csv
read

In [15]:
for d, scores in out.items():
  for params, mean_std in scores.items():
    print(f"{d} {params}: {mean_std}")

RA R=5, K=20, ap: (0.3741666666666667, 0.14387349767533048)
RA R=20, K=20, ap: (0.27074999999999994, 0.08044446842387612)
RA R=5, K=50, ap: (0.2712666666666667, 0.06754781022850902)
RA R=20, K=50, ap: (0.1978, 0.040718054963369756)
RA K=20, roc: (0.5019100643047221, 0.005730192914166177)
RA K=50, roc: (0.5007640257218888, 0.0022920771656665174)
RA K=10 roc: (0.5029939177832332, 0.00898175334969994)
RA K=1 roc: (0.5043478260869565, 0.013043478260869556)
IBD R=5, K=20, ap: (0.3907708333333334, 0.1417815725787969)
IBD R=20, K=20, ap: (0.30068303571428573, 0.11211044737896413)
IBD R=5, K=50, ap: (0.2950527777777777, 0.1117173395598612)
IBD R=20, K=50, ap: (0.2188106746031746, 0.08718679623786386)
IBD K=20, roc: (0.5182881420179408, 0.054864426053822336)
IBD K=50, roc: (0.5133251587088508, 0.039975476126552015)
IBD K=10 roc: (0.5206832388457776, 0.06204971653733262)
IBD K=1 roc: (0.525, 0.075)
